In [1]:
import torch
import torch.nn as nn
import torchvision.datasets as dsets
import torchvision.transforms as transforms
import torch.nn.functional as f 
from torch.autograd import Variable
torch.backends.cudnn.deterministic = True
import pandas as pd
import numpy as np
import torch.utils.data as data_utils
from sklearn.preprocessing import StandardScaler 
from sklearn.model_selection import train_test_split
from sklearn import metrics
import random 
from matplotlib import pyplot as plt
from sklearn import decomposition
from sklearn import manifold
from scipy import stats
from itertools import cycle
import sys
import utilities as ut
from Network import Net
import Network as nn
SEED = 1234
random.seed(SEED)
np.random.seed(SEED)
torch.manual_seed(SEED)
torch.cuda.manual_seed(SEED)
torch.backends.cudnn.deterministic = True
import matplotlib

matplotlib.rcParams["figure.dpi"] = 100


use_cuda = torch.cuda.is_available()
device = torch.device("cuda:0" if use_cuda else "cpu")
torch.backends.cudnn.benchmark = True

#ab y c con 3000 samples, 256 batch y 10000 objetos. 

results = []
num_classes = 2
learning_rate = 0.001
samples = 3000 #
epsilon=0
#for epsilon in [0.1, 0.05, 0.025, 0.15]:
for sc in ['_RRab', '_RRc']: #,'_RRc','_RRab'
    for batch_size in [256]:
        for hidden_size in [100]:
            for aux_loss_activated in [False]:
                for EPS1 in [0.005]:
                    for n in [2500, 5000, 10000]:
                        for opt in [1]:
                            for t in range(15):
                                train_dataset, test_dataset = ut.load_files(dataset=1, subclass=sc)
                                input_size = train_dataset.shape[1]-1

                                if n < 50000:
                                    train_dataset = ut.down_sampling(train_dataset)
                                    train_dataset = train_dataset.sample(n)
                                    print(train_dataset)
                                else: 
                                    trainig_dataset_a = train_dataset[train_dataset.label=='ClassA']
                                    print('shape: ', trainig_dataset_a.shape[0])
                                    n2 = n - trainig_dataset_a.shape[0]
                                    print('clase no RR Lrae', n2)
                                    trainig_dataset_b = train_dataset[~(train_dataset.label=='ClassA')].sample(n2)
                                    train_dataset = pd.concat([trainig_dataset_a, trainig_dataset_b])

                                train_dataset, _ = ut.delete_outliers(train_dataset, test_dataset)

                                train_dataset = ut.sort_columns(train_dataset)
                                test_dataset = ut.sort_columns(test_dataset)

                                test_dataset_pred = test_dataset.copy()
                                train_dataset_pred = train_dataset.copy()

                                try:
                                    data_prior = ut.generate_samples_2D(samples, train_dataset, distribution='uniform')

                                    train_dataset, val_dataset = train_test_split(train_dataset, test_size=0.2, random_state=42)

                                    train_dataset_prior, val_dataset_prior = train_test_split(data_prior, test_size=0.2, random_state=42)
                                    print(train_dataset_prior.columns)
                                    _, _, train_target_prior, train_loader_prior = ut.get_tensors(train_dataset_prior, batch_size)
                                    _, _, val_target_prior, val_loader_prior     = ut.get_tensors(val_dataset_prior, batch_size)
                                    _, _, train_target, train_loader             = ut.get_tensors(train_dataset, batch_size)
                                    _, _, train_target_pred, train_loader_pred   = ut.get_tensors(train_dataset_pred, batch_size)
                                    _, _, val_target, val_loader                 = ut.get_tensors(val_dataset_prior, batch_size)
                                    _, _, test_target, test_loader               = ut.get_tensors(test_dataset, batch_size)
                                    _, _, test_target_pred, test_loader_pred     = ut.get_tensors(test_dataset_pred, batch_size)

                                    net = Net(input_size, hidden_size, hidden_size, num_classes)
                                    net.cuda()

                                    hist_val, hist_train = nn.train(net, train_loader, train_loader_prior, val_loader, test_loader,
                                    EPS1, learning_rate, input_size, aux_loss_activated=aux_loss_activated, patience=10)

                                    acc_train, recall_train, f1_train = nn.get_results(net, train_loader, input_size)
                                    acc_test, recall_test, f1_test  = nn.get_results(net, test_loader, input_size)
                                    results.append([acc_train, acc_test,recall_train, recall_test, f1_train, f1_test, epsilon, batch_size, hidden_size, aux_loss_activated, EPS1, n, opt, sc])
                                    pd.DataFrame(results, columns=['acc_train', 'acc_test','recall_train', 'recall_test','f1_train', 'f1_test',
                                     'epsilon', 'batch_size', 'hidden_size',
                                     'aux_loss_activated', 'EPS1', 'n', 'opt', 'sc']).to_csv('subclasses_07-05-2022-baseline.csv')
                                except Exception as e:
                                    print(e) 
                                    print(str(batch_size)+"-"+str(hidden_size)+"-"+str(aux_loss_activated)+"-"+str(EPS1))

/home/franciscoperez/anaconda3/lib/python3.7/site-packages/pandas/compat/_optional.py:138: UserWarning: Pandas requires version '2.7.0' or newer of 'numexpr' (version '2.6.8' currently installed).
  warnings.warn(msg, UserWarning)
In /home/franciscoperez/anaconda3/lib/python3.7/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle: 
The text.latex.preview rcparam was deprecated in Matplotlib 3.3 and will be removed two minor releases later.
In /home/franciscoperez/anaconda3/lib/python3.7/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle: 
The mathtext.fallback_to_cm rcparam was deprecated in Matplotlib 3.3 and will be removed two minor releases later.
In /home/franciscoperez/anaconda3/lib/python3.7/site-packages/matplotlib/mpl-data/stylelib/_classic_test.mplstyle: Support for setting the 'mathtext.fallback_to_cm' rcParam is deprecated since 3.3 and will be removed two minor releases later; use 'mathtext.fallback : 'cm' instead.
In /home/franciscoperez/anacon

Freq1_harmonics_rel_phase_0
Freq2_harmonics_rel_phase_0
Freq3_harmonics_rel_phase_0
downsampling
21885
369616
done downsampling
        Amplitude  AndersonDarling  Autocor_length  Beyond1Std    CAR_mean  \
5472      0.27550         0.229660               1    0.353333   23.520652   
59067     0.34500         0.000116               1    0.370000   55.028761   
325888    0.24050         0.003151               1    0.353333   26.861221   
315033    0.05400         0.000000               1    0.173333  193.960646   
67839     0.13900         0.000000              11    0.206667    0.071036   
...           ...              ...             ...         ...         ...   
30134     0.35975         0.000006               1    0.348624  188.690262   
77185     0.37150         0.464021               1    0.320000  281.772622   
141661    0.23150         0.008063               1    0.366667  148.558655   
174172    0.29900         0.264227               1    0.377778   53.681618   
168501    0.34

/home/franciscoperez/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


Epochs:  1000
Epoch:  0
training: epoch:  1  loss:  14.785607695579529 -- aux loss:  0.0
validating: epoch:  1  loss:  13.008204102516174
Epoch:  1
training: epoch:  2  loss:  12.749456703662872 -- aux loss:  0.0
validating: epoch:  2  loss:  12.455964028835297
Epoch:  2
training: epoch:  3  loss:  11.39447396993637 -- aux loss:  0.0
validating: epoch:  3  loss:  11.774843692779541
Epoch:  3
training: epoch:  4  loss:  10.705892652273178 -- aux loss:  0.0
validating: epoch:  4  loss:  11.029806017875671
Epoch:  4
training: epoch:  5  loss:  10.297029703855515 -- aux loss:  0.0
validating: epoch:  5  loss:  10.243796586990356
Epoch:  5
training: epoch:  6  loss:  10.051952213048935 -- aux loss:  0.0
validating: epoch:  6  loss:  9.436195522546768
Epoch:  6
training: epoch:  7  loss:  9.90790581703186 -- aux loss:  0.0
validating: epoch:  7  loss:  8.817107886075974
Epoch:  7
training: epoch:  8  loss:  9.57227098941803 -- aux loss:  0.0
validating: epoch:  8  loss:  8.212469637393951
Ep

training: epoch:  44  loss:  8.886737257242203 -- aux loss:  0.0
validating: epoch:  44  loss:  6.003246188163757
Epoch:  44
training: epoch:  45  loss:  8.750626266002655 -- aux loss:  0.0
validating: epoch:  45  loss:  6.0014607310295105
Epoch:  45
training: epoch:  46  loss:  9.43555098772049 -- aux loss:  0.0
validating: epoch:  46  loss:  6.000517308712006
Epoch:  46
training: epoch:  47  loss:  10.533267229795456 -- aux loss:  0.0
validating: epoch:  47  loss:  5.998384028673172
Epoch:  47
training: epoch:  48  loss:  10.003010511398315 -- aux loss:  0.0
validating: epoch:  48  loss:  5.995650559663773
Epoch:  48
training: epoch:  49  loss:  9.58685490489006 -- aux loss:  0.0
validating: epoch:  49  loss:  5.993682831525803
Epoch:  49
training: epoch:  50  loss:  9.27638977766037 -- aux loss:  0.0
validating: epoch:  50  loss:  5.991614073514938
The current loss: 5.991614073514938
the_last_loss: 5.993682831525803
trigger times: 0
recall
tensor(0.9946)
precision
tensor(0.9606)
f1_

...

training: epoch:  955  loss:  33.48546966910362 -- aux loss:  0.0
validating: epoch:  955  loss:  5.951971113681793
Epoch:  955
training: epoch:  956  loss:  34.54067200422287 -- aux loss:  0.0
validating: epoch:  956  loss:  5.951971113681793
Epoch:  956
training: epoch:  957  loss:  33.28788113594055 -- aux loss:  0.0
validating: epoch:  957  loss:  5.951971083879471
Epoch:  957
training: epoch:  958  loss:  33.08489644527435 -- aux loss:  0.0
validating: epoch:  958  loss:  5.951971113681793
Epoch:  958
training: epoch:  959  loss:  33.4514681994915 -- aux loss:  0.0
validating: epoch:  959  loss:  5.951971054077148
Epoch:  959
training: epoch:  960  loss:  33.00924926996231 -- aux loss:  0.0
validating: epoch:  960  loss:  5.951971054077148
The current loss: 5.951971054077148
the_last_loss: 5.951971054077148
trigger times: 0
recall
tensor(0.9976)
precision
tensor(0.9759)
f1_score
tensor(0.9866)
Accuracy of the network on test objects: 97 %
97.59289
recall
tensor(1.)
precision
tenso

training: epoch:  997  loss:  33.04957956075668 -- aux loss:  0.0
validating: epoch:  997  loss:  5.951971024274826
Epoch:  997
training: epoch:  998  loss:  33.0495787858963 -- aux loss:  0.0
validating: epoch:  998  loss:  5.951971024274826
Epoch:  998
training: epoch:  999  loss:  33.049578100442886 -- aux loss:  0.0
validating: epoch:  999  loss:  5.951971024274826
Epoch:  999
training: epoch:  1000  loss:  33.04957735538483 -- aux loss:  0.0
validating: epoch:  1000  loss:  5.951971024274826
The current loss: 5.951971024274826
the_last_loss: 5.951971024274826
trigger times: 0
recall
tensor(0.9955)
precision
tensor(0.9766)
f1_score
tensor(0.9860)
Accuracy of the network on test objects: 97 %
97.66466
recall
tensor(1.)
precision
tensor(1.)
f1_score
tensor(1.)
Accuracy of the network on test objects: 100 %
100.0
recall
tensor(0.9331)
precision
tensor(0.3669)
f1_score
tensor(0.5267)
Accuracy of the network on test objects: 36 %
36.69425
sum mask2 - L1:  tensor(5757, device='cuda:0')
s

/home/franciscoperez/anaconda3/lib/python3.7/site-packages/pandas/core/indexing.py:1817: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


training: epoch:  1  loss:  50.31344574689865 -- aux loss:  0.0
validating: epoch:  1  loss:  13.23579055070877
Epoch:  1
training: epoch:  2  loss:  41.02316960692406 -- aux loss:  0.0
validating: epoch:  2  loss:  12.032041847705841
Epoch:  2
training: epoch:  3  loss:  37.43102565407753 -- aux loss:  0.0
validating: epoch:  3  loss:  10.509066760540009
Epoch:  3
training: epoch:  4  loss:  36.664794862270355 -- aux loss:  0.0
validating: epoch:  4  loss:  8.989462912082672
Epoch:  4
training: epoch:  5  loss:  34.95541027188301 -- aux loss:  0.0
validating: epoch:  5  loss:  7.969510465860367
Epoch:  5
training: epoch:  6  loss:  35.5331591963768 -- aux loss:  0.0
validating: epoch:  6  loss:  7.2899123430252075
Epoch:  6
training: epoch:  7  loss:  38.289201349020004 -- aux loss:  0.0
validating: epoch:  7  loss:  6.904187083244324
Epoch:  7
training: epoch:  8  loss:  34.36679324507713 -- aux loss:  0.0
validating: epoch:  8  loss:  6.6423176527023315
Epoch:  8
training: epoch:  9

KeyboardInterrupt: 

In [ ]:
nn.get_results(net, train_loader, input_size)
nn.get_results(net, test_loader, input_size)

In [ ]:
nn.get_roc_curve(net, test_loader, input_size)

In [ ]:
torch.save(net.state_dict(), 'model.pkl')

In [ ]:
ut.plot_training(hist_val, hist_train)

In [ ]:
fig, ax = plt.subplots(1, 1, figsize=(6,6))
curves, labels, probs_test = ut.get_predictions(net, test_loader_pred, device)
pred_labels = probs_test.argmax(1, keepdim = True)
ut.plot_confusion_matrix(np.round(labels), pred_labels, ax)

In [ ]:
#csv_file = open("size_MLP_noise.csv", "a")
#csv_file.write(str(np.asarray(acc_testing))+","+str(np.asarray(acc_training))+","+str(samples)+","+str(epsilon)+","+str(n)+","+str(hidden_size)+"\n")
#csv_file.close()

In [ ]:
outputs, intermediates, intermediates2, labels = ut.get_representations(net, train_loader, device)
outputs_test, intermediates_test, intermediates2_test, labels_test = ut.get_representations(net, test_loader, device)

In [ ]:
intermediate_pca_data, intermediate_pca_data_test = ut.get_pca(intermediates, data_test=intermediates_test)
fig, axs = plt.subplots(2, 3, figsize=(20,15))
ut.plot_representations(intermediate_pca_data, labels, axs[0, 0])
ut.plot_representations(intermediate_pca_data_test, labels_test, axs[1, 0])
intermediate2_pca_data, intermediate2_pca_data_test = ut.get_pca(intermediates2, data_test=intermediates2_test)
ut.plot_representations(intermediate2_pca_data, labels, axs[0, 1])
ut.plot_representations(intermediate2_pca_data_test, labels_test, axs[1, 1])
output_pca_data, output_pca_data_test = ut.get_pca(outputs, data_test=outputs_test)
ut.plot_representations(output_pca_data, labels, axs[0, 2])
ut.plot_representations(output_pca_data_test, labels_test, axs[1, 2])

In [ ]:
import umap

fig, axs = plt.subplots(2, 3, figsize=(20,15))
print('first')
reducer = umap.UMAP()
print('first ..')
mapper_train = reducer.fit_transform(intermediates.numpy())
print('first ...')
reducer = umap.UMAP()
mapper_test = reducer.fit_transform(intermediates_test.numpy())
ut.plot_representations(mapper_train, labels, axs[0, 0])
ut.plot_representations(mapper_test, labels_test, axs[1, 0])

reducer = umap.UMAP()
mapper_train = reducer.fit_transform(intermediates2.numpy())
reducer = umap.UMAP()
mapper_test = reducer.fit_transform(intermediates2_test.numpy())
ut.plot_representations(mapper_train, labels, axs[0, 1])
ut.plot_representations(mapper_test, labels_test, axs[1, 1])

reducer = umap.UMAP()
mapper_train = reducer.fit_transform(outputs.numpy())
reducer = umap.UMAP()
mapper_test = reducer.fit_transform(outputs_test.numpy())

ut.plot_representations(mapper_train, labels, axs[0, 2])
ut.plot_representations(mapper_test, labels_test, axs[1, 2])

In [ ]:
N_CURVES = 25000

fig, axs = plt.subplots(2, 3, figsize=(20,15))
intermediate_tsne_data, intermediate_tsne_data_test = ut.get_tsne(intermediates, data_test= intermediates_test, n_curves = N_CURVES)
ut.plot_representations(intermediate_tsne_data, labels, axs[0, 0],  n_curves = N_CURVES)
ut.plot_representations(intermediate_tsne_data_test, labels_test, axs[1, 0], n_curves = N_CURVES)

intermediate2_tsne_data, intermediate2_tsne_data_test = ut.get_tsne(intermediates2, data_test=intermediates2_test, n_curves = N_CURVES)
ut.plot_representations(intermediate2_tsne_data, labels, axs[0, 1], n_curves = N_CURVES)
ut.plot_representations(intermediate2_tsne_data_test, labels_test, axs[1, 1], n_curves = N_CURVES)

output_tsne_data, output2_tsne_data_test = ut.get_tsne(outputs, data_test=outputs_test, n_curves = N_CURVES)
ut.plot_representations(output_tsne_data, labels, axs[0, 2], n_curves = N_CURVES)
ut.plot_representations(output2_tsne_data_test, labels_test, axs[1, 2], n_curves = N_CURVES)

In [ ]:
#fig, ax = plt.subplots(1, 1, figsize=(15,15))
#curves, labels, probs_train = ut.get_predictions(net, train_loader_pred, device)
#pred_labels = probs_train.argmax(1, keepdim = True)
#ut.plot_confusion_matrix(np.round(labels), pred_labels, ax)


In [ ]:
pred_labels

In [ ]:
curves, labels, probs_train_sample = ut.get_predictions(net, train_loader, device)

In [ ]:
#N_WEIGHTS = 25
#weights = net.fc2.weight.data
#plot_weights(weights, N_WEIGHTS)

In [ ]:
weights1 = net.fc1.weight.data
w1 = weights1.cpu().numpy().reshape(-1,1)
weights2 = net.fc2.weight.data
w2 = weights2.cpu().numpy().reshape(-1,1)
weights3 = net.fc3.weight.data
w3 = weights3.cpu().numpy().reshape(-1,1)

In [ ]:
fig, (ax1, ax2, ax3) = plt.subplots(1, 3, figsize=(20,15))
ax1.hist(w1, color='black')
ax1.set_xlabel('Layer 1')
ax2.hist(w2, color='black')
ax2.set_xlabel('Layer 2')
ax3.hist(w3, color='black')
ax3.set_xlabel('Layer 3')
plt.show()

In [ ]:
fig, (ax1, ax2) = plt.subplots(2, 1, figsize=(15,15))
curves, labels, probs_train = ut.get_predictions(net, train_loader_pred, device)
pred_labels = torch.argmax(probs_train, 1)
ut.plot_confusion_matrix(np.round(labels), pred_labels, ax1)
curves, labels, probs_test = ut.get_predictions(net, test_loader_pred, device)
pred_labels = torch.argmax(probs_test, 1)
ut.plot_confusion_matrix(np.round(labels), pred_labels, ax2)